### Predicting energy demand
In this notebook, my aim was to develop a LSTM neural network model to forecast demand. The modelling that follows drew inspiration from the following guides written by Jason @ ML mastery:  
https://machinelearningmastery.com/multivariate-time-series-forecasting-lstms-keras/  
and Jakob Aungiers:  
http://www.jakob-aungiers.com/articles/a/LSTM-Neural-Network-for-Time-Series-Prediction/

In [62]:
# Prepare the modelling environment
import os
import psycopg2 as pg
import sqlalchemy as sa
import numpy as np
from numpy import newaxis
import pandas as pd
import plotly.plotly as py
import plotly.graph_objs as go
import plotly.offline as po
from plotly import tools
# To run plotly offline
po.init_notebook_mode(connected=True)

import time
from math import sqrt
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import mean_squared_error
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import LSTM
from keras.layers import Activation

# Set a working directory
os.chdir("C:/Users/Blake/Documents/UTS/36102_iLab_1/Client/")

# Define input parameters
user_name = r"postgres"
user_pass = r"password"
db_name = r"endgame"
server = r"localhost"

# Establishing a connection to postgres
strEngine = r'postgresql://' + user_name+ "@" + server + "/" + db_name
engine = sa.create_engine(strEngine)
connstring = "host='%s' dbname='%s' user='%s' password='%s'" % (server, db_name, user_name, user_pass)
conn = pg.connect(connstring)

#### Extract Data
The following sections will extract both the demand and weather data for modelling

In [63]:
## As usual, extract demand data, but at it's 5 minute level
# Select a region
sqlRegion = 'NSW1'
# Select a date range
sqlLowerDateGE = "2016-01-01"
sqlUpperDateLE = "2016-12-31"

# Exract demand and group it into half hours
sqlDemand = r"select to_char(settlementdate, 'YYYY-MM-DD HH24:MI:SS') as settlementdate \
, totaldemand \
from aemo.demand \
where regionid = '" + sqlRegion + "' \
and settlementdate >= '" + sqlLowerDateGE + "' and settlementdate <= '" + sqlUpperDateLE + "'"

# Retrieve the data
dataDemand = pd.read_sql_query(sqlDemand, con=engine)
# Assign the settlement date as an index 
dataDemand.settlementdate = pd.to_datetime(dataDemand['settlementdate'])
dataDemand = dataDemand.set_index(['settlementdate'])

# Now group it to 30 minute increments
hfhrDemand = dataDemand.groupby(pd.TimeGrouper(freq="30min")).agg({'totaldemand':[np.mean, sum]})

hfhrDemand.columns = ['totaldemand_mean', 'totaldemand_sum']

# Drop missing obs - seems to be missing obs in October every year
hfhrDemand = hfhrDemand.dropna(axis = 0, how = "all")

In [64]:
# Similarly, extract weather data (already at the half hour interval)
sqlStationID = "66137"
stationName = "Bankstown Airport"

sqlWeather = r"select to_char(a.index, 'YYYY-MM-DD HH24:MI:SS') as ts \
, air_temp \
from bom.weather a \
where a.station_id = '" + sqlStationID + "' \
and a.index >= '" + sqlLowerDateGE + "' and a.index <= '" + sqlUpperDateLE + "';"

# Read the data into a dataframe
dataWeather = pd.read_sql_query(sqlWeather, con=engine)

# Correct some variable types
dataWeather.ts = pd.to_datetime(dataWeather['ts'])

# Assign the settlement date as an index 
dataWeather = dataWeather.set_index(['ts'])

In [65]:
# Merge the two datasets together
# Create a new object that brings the two together
dataModel = hfhrDemand.merge(dataWeather, how="left", left_index=True, right_index=True)

# Drop the total demand column and create a lag demand column
dataModel = dataModel.drop(['totaldemand_sum'], 1)
dataModel.columns = ['totaldemand', 'air_temp']

# Drop NaN observtions
dataModel.dropna(inplace=True)

dataModel.info()
dataModel.head()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 17470 entries, 2016-01-01 00:00:00 to 2016-12-31 00:00:00
Data columns (total 2 columns):
totaldemand    17470 non-null float64
air_temp       17470 non-null float64
dtypes: float64(2)
memory usage: 409.5 KB


totaldemand  air_temp
2016-01-01 00:00:00  7013.216667      18.4
2016-01-01 00:30:00  6796.951667      18.3
2016-01-01 01:00:00  6470.815000      17.9
2016-01-01 01:30:00  6173.518333      18.5
2016-01-01 02:00:00  5962.785000      17.0

### Modelling using LSTMs
I will use the keras package with a tensorflow backend to assemble the LSTM. Our goal will be to train the LSTM using a window of data and get the model to predict the next N-steps. There are a few steps required to prepare the data for the model.  
* Extract the pandas dataframe into an array of values  
* Normalise the values - neural networks are sensitive to scale, so the values will be normalised between 0 and 1. The normalisation can be reversed when making predictions.  
* Partition the dataset into training and test sets. The training set will be used for the model to learn, and the test set will be used for model validation
* Create a numpy array of three dimensions for model development:  
    * N - The number of training sequences - think of this as how many sequences to use for training (observations)  
    * W - the window size / sequence length - this is like the size of the time window for training  
    * F - the number of features in each sequence  - these are the predictors the model will use  
* Design the network structure - this example will assemble a very basic model structure. Future usage of this framework should consider optimising the neural network design.  
  
***
#### Modelling approach
The following model designs have been implemented below:  
* Univariate model making single (i.e. next) step predictions  
* Univariate model making a full sequence prediction using predictions made to predict future values  
* Univariate model making multiple predictions over a defined window length  
* Multivate model making single (i.e. next) step predictions  
* Multivate model making a full sequence prediction using predictions made to predict future values  
* Multivate model making multiple predictions over a defined window length  

In [66]:
# Define a function for converting the data into a series of windows
def prep_data(inputData, seq_len):

    # Determine the length of the window
    sequence_length = seq_len + 1
    # Create an empty vector for the result
    result = []
    for index in range(len(inputData) - sequence_length):
        # Append slices of data together i.e 
        # 0 to sequence_length
        # 1 to sequence_length + 1 etc
        result.append(inputData[index: index + sequence_length])
  
    # Convert the result into a numpy array (from a list)
    result = np.array(result)
    
    return result 

# Define a function for normalising data within window
# Normalisation will take place relative to the first observation in that window
def normalise_windows(window_data):
    # Create an empty vector for the result
    normalised_data = []
    base_val = []
    # Iterate through the windows, normalise and append
    for window in window_data:
        base_val_data = window[0]
        base_val.append(base_val_data)
        normalised_window = [((float(p) / float(window[0])) - 1) for p in window]
        normalised_data.append(normalised_window)
        
    normalised_data = np.array(normalised_data)
    base_val = np.array(base_val)
        
    return normalised_data, base_val

# Define another function to return the data to the original scale
# Undo the effects of normalisation
def return_original_scale(norm_val, base_val):
    
    rescaled = (norm_val + 1) * base_val
    
    return rescaled

def return_original_scale_multiple(norm_val, base_val, prediction_len):
    
    # Create an empty an empty array
    seq_base = []

    # First loop over number of sequences
    for i in range(int(len(base_val) / prediction_len)):
        
        # Second loop through the number of predictions
        # Repeat the reference value
        for j in range(prediction_len):
            seq_base.append(base_val[i * prediction_len])
            
    seq_base = np.array(seq_base)
            
    # Reshape the normalised predictions
    # Reduce the dimensionality of the dataset, back into a single array
    newRowDim = norm_val.shape[0] * norm_val.shape[1]
    norm_val_reshaped = norm_val.reshape(newRowDim)

    # Cross multiply the two arrays to rescale the predictions
    rescaled = seq_base * (norm_val_reshaped + 1)
    
    return rescaled, newRowDim

# Define a function for partition data into training and test sets
def split_data(inputData, partitionPoint):
    
    # Develop a partition to split the dataset into training and test set
    row = round(partitionPoint * inputData.shape[0])
 
    #np.random.shuffle(train)
    # Create training sets 
    train = inputData[:int(row), :]
    x_train = train[:, :-1]
    y_train = train[:, -1]
    
    # Create testing sets
    x_test = inputData[int(row):, :-1]
    y_test = inputData[int(row):, -1]
    
    return [x_train, y_train, x_test, y_test, row]

# Define a function for shaping the data into appropriately dimensioned tensors for Keras
def shape_data(inputData, featureNum):
    
    # Reshape the input array
    result = np.reshape(inputData, (inputData.shape[0], inputData.shape[1], featureNum))
    
    return result

In [67]:
## Define a function for assembling the LSTM
def build_model(layers, inputTrain):
    
    model = Sequential()
   
    model.add(LSTM(layers[0], input_shape=(inputTrain.shape[1], inputTrain.shape[2]), return_sequences=True))
    model.add(LSTM(layers[1]))
    
    model.add(Dense(layers[2]))
    model.add(Activation("linear"))

    start = time.time()
    model.compile(loss="mse", optimizer="rmsprop")
    
    print("> Compilation Time : ", time.time() - start)
    
    return model

In [68]:
## Functions for predictions
# Define a function for predictin
def predict_point_by_point(model, data):
    
    # Predict each timestep given the last sequence of true data
    # Effectively predicting 1 step ahead each time
    predicted = model.predict(data)
    predicted = np.reshape(predicted, (predicted.size,))
    return predicted

def predict_sequence_full(model, data, window_size):
    
    # Model is the LSTM
    # data is x_test - the test segment of predictors
    # window size is the same length as the window size used to build the model
    
    # Begin with starting point
    curr_frame = data[0]
    
    # Create an empty vector to hold predictions
    predicted = []
    
    # Loop over the length of the X_train dataset
    for i in range(len(data)):
        #print(i)
        #print("Predicting frame")
        #print(curr_frame[newaxis,:,:])
        # Append the result to the predicted vector
        
        if(i <= 1):
            print("Predicting frame")
            print(curr_frame)
        
        predicted.append(model.predict(curr_frame[newaxis,:,:])[0,0])
        # Make space in the predicting frame for the new prediction
        curr_frame = curr_frame[1:]
        # Insert the prediction to the end of the frame used for making predictions
        curr_frame = np.insert(curr_frame # Insert into the current frame
                               , [window_size - 1] # The position to insert
                               , predicted[-1] # The values to insert (the latest prediction)
                               , axis = 0) # The row / col wise insert

        if(i <= 1):
            print("Predictions")
            print(predicted)
    
    return predicted

def predict_sequences_multiple(model, data, window_size, prediction_len):
    # Model - the LSTM model object
    # Data - testing data 
    # Window size is - how long a sequence to use for making predictions 
    # Prediction length - how many periods to make an estimate for
    
    # Create an empty vector of predicted sequences
    prediction_seqs = []
    
    # Iterate over multiple chunks of the data
    for i in range(int(len(data) / prediction_len)):
        
        # Create a sequence used for prediction
        curr_frame = data[i * prediction_len]
        if (i <= 1):
            print("Starting sequence of true test values")
            print(curr_frame)
            
        # Create an array to store predictions made
        predicted = []
        
        # The second loop is to iterate through the prediction length
        for j in range(prediction_len):
            
            predicted.append(model.predict(curr_frame[newaxis,:,:])[0,0])
            if (i <= 1):
                print("Make a prediction using the model")
                print(predicted)
            curr_frame = curr_frame[1:]
            #print("Append the latest prediction as the last value in the window")
            curr_frame = np.insert(curr_frame, [window_size-1], predicted[-1], axis=0)
        prediction_seqs.append(predicted)
        if(i <= 1):
            print("Predicted sequences")
            print(prediction_seqs)
        
    return prediction_seqs

#### Univariate single-step model
* A window of historical demand will be used to predict demand  
* Predictions made using the test data, will be done a shifting window of the true test data to predict the next value in sequence (single-step). This will be done using the *predict_point_by_point* function

In the following section, the data will be transformed into a series of sequences

In [69]:
## Extract the values
dataValues = dataModel['totaldemand'].values.tolist()

## Prepare the data for modelling
# Choose a sequence length (data is in half hour intervals)
inputSeqLen = 1008
dataPrep = prep_data(inputData = dataValues, seq_len = inputSeqLen)
print("Output the type, shape and samples for the prepared data")
print(type(dataPrep))
print(dataPrep.shape)
print(dataPrep[0:2])

Output the type, shape and samples for the prepared data
<class 'numpy.ndarray'>
(16461, 1009)
[[ 7013.21666667  6796.95166667  6470.815      ...,  8228.76        8028.99
   7768.75666667]
 [ 6796.95166667  6470.815       6173.51833333 ...,  8028.99        7768.75666667
   7520.72333333]]


Next, we will normalise the values within each sequence

In [70]:
## Normalise the values within each window
# keep the base for reverting to original scale later
dataNorm, dataBase = normalise_windows(window_data = dataPrep)
print("Output the type, shape and samples of the normalised data")
print(type(dataNorm))
print(dataNorm.shape)
print(dataNorm[0:2])

Output the type, shape and samples of the normalised data
<class 'numpy.ndarray'>
(16461, 1009)
[[ 0.         -0.03083678 -0.07733993 ...,  0.1733218   0.14483701
   0.10773088]
 [ 0.         -0.04798278 -0.09172249 ...,  0.18126337  0.14297659
   0.10648475]]


Parition the data into training and test sets

In [71]:
## Partition the data into training and test sets
# Split the data into 75% training and 25% test
inputPartition = 0.75
X_train, y_train, X_test, y_test, rowID = split_data(inputData = dataNorm, partitionPoint = inputPartition)
print("Output the shape and samples for the predictors")
print(X_train.shape)
print(X_train[0:2])
print("Output the shape and samples for the outcome")
print(y_train.shape)
print(y_train[0:2])

Output the shape and samples for the predictors
(12346, 1008)
[[ 0.         -0.03083678 -0.07733993 ...,  0.21847322  0.1733218
   0.14483701]
 [ 0.         -0.04798278 -0.09172249 ...,  0.21065448  0.18126337
   0.14297659]]
Output the shape and samples for the outcome
(12346,)
[ 0.10773088  0.10648475]


The following step is important to reshape the sequence data into a suitable shape for Keras and Tensorflow. The shape specifies the N, W, and F dimensions described earlier. 

In [72]:
## Shape the predicting data into tensors for the model
X_train = shape_data(inputData = X_train, featureNum = 1)
X_test = shape_data(inputData = X_test, featureNum = 1)
print("Output the shape and samples after reshaping into tensors")
print(X_train.shape)
print(X_train[0:2])

Output the shape and samples after reshaping into tensors
(12346, 1008, 1)
[[[ 0.        ]
  [-0.03083678]
  [-0.07733993]
  ..., 
  [ 0.21847322]
  [ 0.1733218 ]
  [ 0.14483701]]

 [[ 0.        ]
  [-0.04798278]
  [-0.09172249]
  ..., 
  [ 0.21065448]
  [ 0.18126337]
  [ 0.14297659]]]


In this next chunk, the model will be assembled and fitted on the the training data

In [73]:
# Build the model
# Define the number of epochs (learning iterations)
inputEpochs = 10

# Define the model structure. The first parameter to this function is a list of inputs used to assemble the model
# The first is the number of neurons in the first hidden layer of the neural network
# The second is the number of neurons in the second hidden layer of the neural networks
modelUSS = build_model([25, 10, 1], inputTrain = X_train)

# Fit the model
fitUSS = modelUSS.fit(X_train, y_train, batch_size = 512, epochs=inputEpochs, validation_split = 0.05)

# Plot the training loss
plotTrainLoss = fitUSS.history['loss']
plotTestLoss = fitUSS.history['val_loss']
# Structure the results into a dataframe
plotLoss = pd.DataFrame({'epoch': list(range(1, inputEpochs + 1))
                         , 'train': plotTrainLoss
                         , 'test': plotTestLoss})
plotLoss = plotLoss.set_index(['epoch'])

# Plot the results
plotTrainLoss = go.Scatter(x = plotLoss.index, y = plotLoss.train, name = "Train", mode = 'line')
plotTestLoss = go.Scatter(x = plotLoss.index, y = plotLoss.test, name = "Test", mode = 'line')

plotData = [plotTrainLoss, plotTestLoss]
plotLayout = go.Layout(title="Training and test loss by epoch",
                xaxis=dict(title='Epoch'),
                yaxis=dict(title='MSE'))

plotFig = go.Figure(data = plotData, layout = plotLayout)
po.iplot(plotFig)

> Compilation Time :  0.031230688095092773
Train on 11728 samples, validate on 618 samples
Epoch 1/10
11728/11728 [==============================] - 167s - loss: 0.0085 - val_loss: 0.0028
Epoch 2/10
11728/11728 [==============================] - 173s - loss: 0.0067 - val_loss: 0.0033
Epoch 3/10
11728/11728 [==============================] - 177s - loss: 0.0055 - val_loss: 0.0020
Epoch 4/10
11728/11728 [==============================] - 185s - loss: 0.0043 - val_loss: 0.0026
Epoch 5/10
11728/11728 [==============================] - 174s - loss: 0.0035 - val_loss: 0.0023
Epoch 6/10
11728/11728 [==============================] - 173s - loss: 0.0030 - val_loss: 0.0014
Epoch 7/10
11728/11728 [==============================] - 183s - loss: 0.0026 - val_loss: 0.0013
Epoch 8/10
11728/11728 [==============================] - 173s - loss: 0.0022 - val_loss: 0.0012
Epoch 9/10
11728/11728 [==============================] - 176s - loss: 0.0019 - val_loss: 8.6628e-04
Epoch 10/10
11728/11728 [=======

In the following chunks, the model is used to make predictions on the test set. The predictions will be normalised, so another function *return_original_scale* will be used to revert the normalised values back to the original scale for comparison to the test Y values.

In [74]:
# Make single step predictions with the model
predictUSS = predict_point_by_point(data = X_test, model = modelUSS)

In [75]:
# Reverse the normalisation
referenceVal = dataBase[rowID:]
y_test_scaled = return_original_scale(norm_val = y_test, base_val = referenceVal)
predictUSS_scaled = return_original_scale(norm_val = predictUSS, base_val = referenceVal)

print(predictUSS_scaled[0:3])
print(y_test_scaled[0:3])

[ 6041.45614684  6390.93058299  6889.98133783]
[ 6481.78666667  6962.62166667  7420.27166667]


In [76]:
# Prepare a vector to act as an ID columns
idData = dataModel.iloc[(rowID + inputSeqLen):-1,:]

# Compare the predictions with the test data
plotResultsUSS = pd.DataFrame({'id': idData.index
                               , 'actual':y_test_scaled
                               , 'predict':predictUSS_scaled})

# Calculate RMSE
rmse = sqrt(mean_squared_error(y_test_scaled, predictUSS_scaled))
print('Test RMSE: %.3f' % rmse)

# Plot the result
plotActuals = go.Scatter(x = plotResultsUSS.id, y = plotResultsUSS.actual, name = "Actuals", mode = 'line')
plotPredicted = go.Scatter(x = plotResultsUSS.id, y = plotResultsUSS.predict, name = "Predicted", mode = 'line')

plotData = [plotActuals, plotPredicted]
plotLayout = go.Layout(title="Actuals vs Predicted - Univariate, Single-step LSTM",
                xaxis=dict(title='Time (half hour)'),
                yaxis=dict(title='Demand (MW)'))

plotFig = go.Figure(data = plotData, layout = plotLayout)
po.iplot(plotFig)

Test RMSE: 275.936


This chart shows a close relationship between the observed values and the predicted values this is because the previous value in the sequence will be highly correlated with the next value of the sequence. Essentially the model can make a small guess of the next value from its current value and not be too far off the actual value. 

#### Univariate multi-step model
* A window of historical demand will be used to predict future demand (univariate)  
* Predictions made using the start of the test data and will be used to make subsequent predictions for remainder of the sequence length. This will be initially done using the *predict_sequence_full* function  
* For a different type of multi-step prediction, the *predict_sequences_multiple* function will be used to make multiple predictions of sequences of a defined length.

In [77]:
# Use true data from the test data for a defined window, and then use model predictions for the rest of the sequence
predictUMS = predict_sequence_full(data = X_test, model = modelUSS, window_size = inputSeqLen)

Predicting frame
[[ 0.        ]
 [ 0.04765544]
 [ 0.10372114]
 ..., 
 [-0.00743246]
 [-0.00581353]
 [ 0.02929974]]
Predictions
[0.0052135824]
Predicting frame
[[ 0.04765544]
 [ 0.10372114]
 [ 0.19612165]
 ..., 
 [-0.00581353]
 [ 0.02929974]
 [ 0.00521358]]
Predictions
[0.0052135824, 0.021469204]


In [78]:
# Reverse the normalisation
predictUMS_scaled = (np.array(predictUMS) + 1) * referenceVal[0]
print(predictUMS_scaled[0:3])
print(y_test_scaled[0:3])

[ 6041.45605469  6139.15429688  6251.80957031]
[ 6481.78666667  6962.62166667  7420.27166667]


In [79]:
# Compare the predictions with the test data
plotResultsUMS = pd.DataFrame({'id': idData.index
                               , 'actual':y_test_scaled
                               , 'predict':predictUMS_scaled})

# Calculate RMSE
rmse = sqrt(mean_squared_error(y_test_scaled, predictUMS_scaled))
print('Test RMSE: %.3f' % rmse)

# Plot the result
plotActuals = go.Scatter(x = plotResultsUMS.id, y = plotResultsUMS.actual, name = "Actuals", mode = 'line')
plotPredicted = go.Scatter(x = plotResultsUMS.id, y = plotResultsUMS.predict, name = "Predicted", mode = 'line')

plotData = [plotActuals, plotPredicted]
plotLayout = go.Layout(title="Actuals vs Predicted - Univariate, Multi-step LSTM - Full sequence prediction",
                xaxis=dict(title='Time (half hour)'),
                yaxis=dict(title='Demand (MW)'))

plotFig = go.Figure(data = plotData, layout = plotLayout)
po.iplot(plotFig)

Test RMSE: 1623.400


This model relies on predictions made to make future predictions for the entirety of the test set. This is the most difficult type of sequence prediction because the effect of errors compound over time. As you can see in the plot above, the model makes a guess using true test data early on, but reaches a stasis level when a naive prediction ensues. 
***
The following type of multi-step prediction will make predictions of 24 hours using previously predicted values. After 24 hours (48 periods) have been predicted in this way, true test data will be used to make predictions for another 24 hours. 

In [80]:
# Make multi-step predictions, but instead of making a full sequence prediction 
inputPredLen = 48
predictUMS = predict_sequences_multiple(data = X_test
                                        , model = modelUSS
                                        , window_size = inputSeqLen
                                        , prediction_len = inputPredLen)
#print(predictUMS[0:3])
predictUMS = np.array(predictUMS)

Starting sequence of true test values
[[ 0.        ]
 [ 0.04765544]
 [ 0.10372114]
 ..., 
 [-0.00743246]
 [-0.00581353]
 [ 0.02929974]]
Make a prediction using the model
[0.0052135824]
Make a prediction using the model
[0.0052135824, 0.021469204]
Make a prediction using the model
[0.0052135824, 0.021469204, 0.040213451]
Make a prediction using the model
[0.0052135824, 0.021469204, 0.040213451, 0.060622618]
Make a prediction using the model
[0.0052135824, 0.021469204, 0.040213451, 0.060622618, 0.081518032]
Make a prediction using the model
[0.0052135824, 0.021469204, 0.040213451, 0.060622618, 0.081518032, 0.10164756]
Make a prediction using the model
[0.0052135824, 0.021469204, 0.040213451, 0.060622618, 0.081518032, 0.10164756, 0.11987912]
Make a prediction using the model
[0.0052135824, 0.021469204, 0.040213451, 0.060622618, 0.081518032, 0.10164756, 0.11987912, 0.1353187]
Make a prediction using the model
[0.0052135824, 0.021469204, 0.040213451, 0.060622618, 0.081518032, 0.10164756, 0.

Make a prediction using the model
[0.0052135824, 0.021469204, 0.040213451, 0.060622618, 0.081518032, 0.10164756, 0.11987912, 0.1353187, 0.14736092, 0.15568884, 0.16024105, 0.16116387, 0.15876172, 0.15345313, 0.14573573, 0.13615848, 0.12530032, 0.11375128, 0.10209417, 0.090885147, 0.080632277, 0.071773708, 0.064656273, 0.059517171, 0.056471676, 0.05550839, 0.056493845, 0.059186138, 0.063257009, 0.068320036, 0.073961161, 0.079769738, 0.085365914, 0.090422519]
Make a prediction using the model
[0.0052135824, 0.021469204, 0.040213451, 0.060622618, 0.081518032, 0.10164756, 0.11987912, 0.1353187, 0.14736092, 0.15568884, 0.16024105, 0.16116387, 0.15876172, 0.15345313, 0.14573573, 0.13615848, 0.12530032, 0.11375128, 0.10209417, 0.090885147, 0.080632277, 0.071773708, 0.064656273, 0.059517171, 0.056471676, 0.05550839, 0.056493845, 0.059186138, 0.063257009, 0.068320036, 0.073961161, 0.079769738, 0.085365914, 0.090422519, 0.094680421]
Make a prediction using the model
[0.0052135824, 0.021469204, 0

Make a prediction using the model
[-0.012647603, 0.0080692442]
Make a prediction using the model
[-0.012647603, 0.0080692442, 0.032247227]
Make a prediction using the model
[-0.012647603, 0.0080692442, 0.032247227, 0.058068804]
Make a prediction using the model
[-0.012647603, 0.0080692442, 0.032247227, 0.058068804, 0.083728448]
Make a prediction using the model
[-0.012647603, 0.0080692442, 0.032247227, 0.058068804, 0.083728448, 0.1076107]
Make a prediction using the model
[-0.012647603, 0.0080692442, 0.032247227, 0.058068804, 0.083728448, 0.1076107, 0.12842408]
Make a prediction using the model
[-0.012647603, 0.0080692442, 0.032247227, 0.058068804, 0.083728448, 0.1076107, 0.12842408, 0.14526962]
Make a prediction using the model
[-0.012647603, 0.0080692442, 0.032247227, 0.058068804, 0.083728448, 0.1076107, 0.12842408, 0.14526962, 0.15764423]
Make a prediction using the model
[-0.012647603, 0.0080692442, 0.032247227, 0.058068804, 0.083728448, 0.1076107, 0.12842408, 0.14526962, 0.1576442

Make a prediction using the model
[-0.012647603, 0.0080692442, 0.032247227, 0.058068804, 0.083728448, 0.1076107, 0.12842408, 0.14526962, 0.15764423, 0.16539545, 0.16865253, 0.16775304, 0.16317925, 0.15550862, 0.14537816, 0.13345975, 0.12044044, 0.10700504, 0.093817361, 0.081497833, 0.070598781, 0.061578423, 0.054776203, 0.050393254, 0.048481304, 0.048942052, 0.05153846, 0.055917274, 0.061640486, 0.068222255, 0.07516738, 0.082006961, 0.088327885, 0.093794085, 0.098159149, 0.10127006]
Make a prediction using the model
[-0.012647603, 0.0080692442, 0.032247227, 0.058068804, 0.083728448, 0.1076107, 0.12842408, 0.14526962, 0.15764423, 0.16539545, 0.16865253, 0.16775304, 0.16317925, 0.15550862, 0.14537816, 0.13345975, 0.12044044, 0.10700504, 0.093817361, 0.081497833, 0.070598781, 0.061578423, 0.054776203, 0.050393254, 0.048481304, 0.048942052, 0.05153846, 0.055917274, 0.061640486, 0.068222255, 0.07516738, 0.082006961, 0.088327885, 0.093794085, 0.098159149, 0.10127006, 0.10306425]
Make a predi

In [81]:
predictUMS_scaled, newRowDim = return_original_scale_multiple(norm_val = predictUMS
                                                              , base_val = referenceVal
                                                              , prediction_len = inputPredLen)

In [82]:
# Trim the arrays for incomplete sequences
idData = idData.iloc[0:newRowDim]
y_test_scaled_trim = y_test_scaled[0:newRowDim]

# Calculate RMSE
rmse = sqrt(mean_squared_error(y_test_scaled_trim, predictUMS_scaled))
print('Test RMSE: %.3f' % rmse)

# Compare the predictions with the test data
plotResultsUMS = pd.DataFrame({'id': idData.index
                               , 'actual':y_test_scaled_trim
                               , 'predict':predictUMS_scaled})

# Plot the result
plotActuals = go.Scatter(x = plotResultsUMS.id, y = plotResultsUMS.actual, name = "Actuals", mode = 'line')
plotPredicted = go.Scatter(x = plotResultsUMS.id, y = plotResultsUMS.predict, name = "Predicted", mode = 'line')

plotData = [plotActuals, plotPredicted]
plotLayout = go.Layout(title="Actuals vs Predicted - Univariate, Multi-step LSTM - Predicting sequences of x periods",
                xaxis=dict(title='Time (half hour)'),
                yaxis=dict(title='Demand (MW)'))

plotFig = go.Figure(data = plotData, layout = plotLayout)
po.iplot(plotFig)

Test RMSE: 1218.674


The plot shows a better prediction can be made using this method (compared to the full sequence prediction). The model has been able to predict the double hump of energy demand for 'regular' days (no extreme spikes in demand), but generally lacks the ability to predict the spikes in demand. Thinking back to what the model has to learn from, we've only fed it historical demand data so it will be limited in its capability to predict the shocks with only this information. Furthermore, a longer window of sequences should be used for training as there are probably seasonal effects not being captured well by this model.

#### Mulitvariate single-step model
* A window of historical demand and air temperature will be used to predict demand (multivariate)  
* Predictions made using the test data, will be done a shifting window of the true test data to predict the next value in sequence (single-step). This will be done using the *predict_point_by_point* function  
  
Some of the functions written previously have had to be adapted to cater for multi-dimensional inputs. These functions are prefixed with a *mv_*.  
  
Otherwise the process of data preparation and modelling is very similar to the previous examples.

In [93]:
# Create a function to normalise the variables
def mv_prep_data(inputData, seq_len):

    # Determine the length of the window
    sequence_length = seq_len + 1
    # Create an empty vector for the result
    result = []
    for index in range(len(inputData) - sequence_length):
        # Append slices of data together i.e 
        # 0 to sequence_length
        # 1 to sequence_length + 1 etc
        result.append(inputData[index: index + sequence_length])

    # Convert the result into a numpy array (from a list)
    result = np.array(result)
    
    return result 

# Define a function for normalising data within window
# Normalisation will take place relative to the first observation in that window
def mv_normalise_windows(window_data):
    
    # Create an empty vector for the result
    normalised_data = []
    # Create an empty vector for the values required to undo the normalisation
    base_data = []
    # First iteration is over the sequences passed in
    for window in window_data:
        base_val = window[0]
        base_data.append(base_val)    
        normalised_feature = [((window[i] / window[0]) - 1) for i in range(window.shape[0])] 
        normalised_data.append(normalised_feature)

    normalised_data = np.array(normalised_data)
    base_data = np.array(base_data)
    #print(normalised_data)    
    #print(base_data)
    
    return normalised_data, base_data

def mv_return_original_scale(norm_val, base_val):
    
    rescaled = (norm_val + 1) * base_val
    
    return rescaled

# Define a function for partition data into training and test sets
def mv_split_data(inputData, partitionPoint, outcomeCol):
    
    # Develop a partition to split the dataset into training and test set
    row = round(partitionPoint * inputData.shape[0])
 
    #np.random.shuffle(train)
    # Create training sets 
    train = inputData[:int(row), :]
    x_train = train[:, :-1]
    y_train = train[:, -1]
    
    y_train_y = y_train[: , outcomeCol]
    # We should also keep the other variable values
    y_train_x = y_train[: , (outcomeCol + 1)]
    
    # Create testing sets
    x_test = inputData[int(row):, :-1]
    y_test = inputData[int(row):, -1]
    y_test_y = y_test[: , outcomeCol]
    y_test_x = y_test[:, (outcomeCol + 1)]
    
    return [x_train, y_train_y, x_test, y_test_y, row, y_train_x, y_test_x]

# Define a function for shaping the data into appropriately dimensioned tensors for Keras
# I think the data is already in the right shape...
#def mv_shape_data(inputData, featureNum):
    
    # Reshape the input array
    #result = np.reshape(inputData, (inputData.shape[0], inputData.shape[1], featureNum))
    
    #a = [[y_train[i][j] for i in range(0,len(y_train))] for j in range(1)]
    #print(a)
    #b = np.array(a)
    #b = b.reshape(len(y_train),)
    #print(b.shape)
    #print(b[0:3])
    
    #return result

In [110]:
def mv_predict_sequence_full(model, data, window_size, excess_predictors):
    
    # Model is the LSTM
    # data is x_test - the test segment of predictors
    # window size is the same length as the window size used to build the model
    
    # Begin with starting point
    curr_frame = data[0]
    
    # Create an empty vector to hold predictions
    predicted = []
    
    # Loop over the length of the X_train dataset
    for i in range(len(data)):
        #print(i)
        #print("Predicting frame")
        #print(curr_frame[newaxis,:,:])
        # Append the result to the predicted vector
        
        if(i <= 1):
            print("Predicting frame")
            print(curr_frame)
        
        predicted.append(model.predict(curr_frame[newaxis,:,:])[0,0])
        
        new_obs = [predicted[-1], excess_predictors[i]]
        if(i <= 1):
            print("Excess X")
            print(excess_predictors[i])
            print("Row to insert")
            print(new_obs)
        
        # Make space in the predicting frame for the new prediction
        curr_frame = curr_frame[1:]
        # Insert the prediction to the end of the frame used for making predictions
        curr_frame = np.insert(curr_frame # Insert into the current frame
                               , [window_size - 1] # The position to insert
                               #, predicted[-1] # The values to insert (the latest prediction). In this case we also need 
                               # to insert the temperature values
                               , new_obs
                               , axis = 0) # The row / col wise insert

        if(i <= 1):
            print("Predictions")
            print(predicted)
    
    return predicted

def mv_predict_sequences_multiple(model, data, window_size, prediction_len, excess_predictors):
    # Model - the LSTM model object
    # Data - testing data 
    # Window size is - how long a sequence to use for making predictions 
    # Prediction length - how many periods to make an estimate for
    
    # Create an empty vector of predicted sequences
    prediction_seqs = []
    
    xs = 0
    # Iterate over multiple chunks of the data
    for i in range(int(len(data) / prediction_len)):
        
        # Create a sequence used for prediction
        curr_frame = data[i * prediction_len]
        if (i <= 1):
            print("Starting sequence of true test values")
            print(curr_frame)
            
        # Create an array to store predictions made
        predicted = []
        
        # The second loop is to iterate through the prediction length
        for j in range(prediction_len):
            
            predicted.append(model.predict(curr_frame[newaxis,:,:])[0,0])
            
            new_obs = [predicted[-1], excess_predictors[xs]]
            if (i <= 1):
                print("New observations for making predictions")
                print(new_obs)
            
            if (i <= 1):
                print("Make a prediction using the model")
                print(predicted)
            
            curr_frame = curr_frame[1:]
            if (i <= 1):
                print("Shifted current frame")
                print(curr_frame)
                
            # Append the latest prediction as the last value in the window
            curr_frame = np.insert(curr_frame
                                   , [window_size-1]
                                   , new_obs
                                   , axis=0)
            xs = xs + 1
            
            if (i <= 1):
                print("Filled current frame for next prediction")
                print(curr_frame)
                
        prediction_seqs.append(predicted)
        if(i <= 1):
            print("Predicted sequences")
            print(prediction_seqs)
        
    return prediction_seqs

In [111]:
## Extract the values
dataValues = dataModel.values.tolist()
print(dataValues[0:3])

## Prepare the data for modelling
# Choose a sequence length (data is in half hour intervals)
inputSeqLen = 1008
dataPrep = mv_prep_data(inputData = dataValues, seq_len = inputSeqLen)
print("Output the shape and samples for the prepared data")
print(dataPrep.shape)
print(dataPrep[0:3])


[[7013.216666666667, 18.4], [6796.951666666667, 18.3], [6470.815, 17.9]]
Output the shape and samples for the prepared data
(16461, 1009, 2)
[[[ 7013.21666667    18.4       ]
  [ 6796.95166667    18.3       ]
  [ 6470.815         17.9       ]
  ..., 
  [ 8228.76          23.4       ]
  [ 8028.99          23.4       ]
  [ 7768.75666667    23.4       ]]

 [[ 6796.95166667    18.3       ]
  [ 6470.815         17.9       ]
  [ 6173.51833333    18.5       ]
  ..., 
  [ 8028.99          23.4       ]
  [ 7768.75666667    23.4       ]
  [ 7520.72333333    23.4       ]]

 [[ 6470.815         17.9       ]
  [ 6173.51833333    18.5       ]
  [ 5962.785         17.        ]
  ..., 
  [ 7768.75666667    23.4       ]
  [ 7520.72333333    23.4       ]
  [ 7212.985         23.4       ]]]


In [112]:
# Normalise the windows
dataNorm, dataBase = mv_normalise_windows(dataPrep)
print(dataNorm[0:2])
print(dataBase[0:2])

[[[ 0.          0.        ]
  [-0.03083678 -0.00543478]
  [-0.07733993 -0.02717391]
  ..., 
  [ 0.1733218   0.27173913]
  [ 0.14483701  0.27173913]
  [ 0.10773088  0.27173913]]

 [[ 0.          0.        ]
  [-0.04798278 -0.02185792]
  [-0.09172249  0.01092896]
  ..., 
  [ 0.18126337  0.27868852]
  [ 0.14297659  0.27868852]
  [ 0.10648475  0.27868852]]]
[[ 7013.21666667    18.4       ]
 [ 6796.95166667    18.3       ]]


In [113]:
## Partition the data into training and test sets
# Split the data into 75% training and 25% test
inputPartition = 0.75
X_train, y_train, X_test, y_test, rowID, y_train_x, y_test_x = mv_split_data(inputData = dataNorm
                                                                             , partitionPoint = inputPartition
                                                                             , outcomeCol = 0)

print(X_test.shape)
print(X_test[0:4])
print("Test y")
print(y_test.shape)
print(y_test[0:3])
print("Excess predictor")
print(y_test_x.shape)
print(y_test_x[0:3])

(4115, 1008, 2)
[[[ 0.          0.        ]
  [ 0.04765544 -0.02758621]
  [ 0.10372114 -0.04827586]
  ..., 
  [-0.00743246 -0.36551724]
  [-0.00581353 -0.35172414]
  [ 0.02929974 -0.42068966]]

 [[ 0.          0.        ]
  [ 0.0535154  -0.0212766 ]
  [ 0.14171283 -0.0070922 ]
  ..., 
  [-0.05103679 -0.33333333]
  [-0.01752074 -0.40425532]
  [ 0.02942094 -0.37588652]]

 [[ 0.          0.        ]
  [ 0.08371726  0.01449275]
  [ 0.1761318   0.07246377]
  ..., 
  [-0.06742772 -0.39130435]
  [-0.02287054 -0.36231884]
  [ 0.04961535 -0.32608696]]

 [[ 0.          0.        ]
  [ 0.0852755   0.05714286]
  [ 0.12504643  0.07857143]
  ..., 
  [-0.09835388 -0.37142857]
  [-0.03146754 -0.33571429]
  [ 0.03219367 -0.37142857]]]
Test y
(4115,)
[ 0.07847844  0.10578593  0.11860609]
Excess predictor
(4115,)
[-0.39310345 -0.34042553 -0.36231884]


In [114]:
# Build the model
inputEpochs = 10
modelMSS = build_model([25, 10, 1], inputTrain = X_train)

fitMSS = modelMSS.fit(X_train, y_train, batch_size = 512, epochs=inputEpochs, validation_split = 0.05)

# Plot the training loss
plotTrainLoss = fitMSS.history['loss']
plotTestLoss = fitMSS.history['val_loss']
# Structure the results into a dataframe
plotLoss = pd.DataFrame({'epoch': list(range(1, inputEpochs + 1))
                         , 'train': plotTrainLoss
                         , 'test': plotTestLoss})
plotLoss = plotLoss.set_index(['epoch'])

# Plot the results
plotTrainLoss = go.Scatter(x = plotLoss.index, y = plotLoss.train, name = "Train", mode = 'line')
plotTestLoss = go.Scatter(x = plotLoss.index, y = plotLoss.test, name = "Test", mode = 'line')

plotData = [plotTrainLoss, plotTestLoss]
plotLayout = go.Layout(title="Training and test loss by epoch",
                xaxis=dict(title='Epoch'),
                yaxis=dict(title='MSE'))

plotFig = go.Figure(data = plotData, layout = plotLayout)
po.iplot(plotFig)

> Compilation Time :  0.025018692016601562
Train on 11728 samples, validate on 618 samples
Epoch 1/10
11728/11728 [==============================] - 224s - loss: 0.0074 - val_loss: 0.0023
Epoch 2/10
11728/11728 [==============================] - 196s - loss: 0.0058 - val_loss: 0.0024
Epoch 3/10
11728/11728 [==============================] - 195s - loss: 0.0048 - val_loss: 0.0022
Epoch 4/10
11728/11728 [==============================] - 198s - loss: 0.0041 - val_loss: 0.0017
Epoch 5/10
11728/11728 [==============================] - 215s - loss: 0.0034 - val_loss: 0.0021
Epoch 6/10
11728/11728 [==============================] - 211s - loss: 0.0029 - val_loss: 0.0017
Epoch 7/10
11728/11728 [==============================] - 217s - loss: 0.0024 - val_loss: 0.0013
Epoch 8/10
11728/11728 [==============================] - 196s - loss: 0.0021 - val_loss: 0.0013
Epoch 9/10
11728/11728 [==============================] - 206s - loss: 0.0019 - val_loss: 0.0010
Epoch 10/10
11728/11728 [===========

In [115]:
# Make single step predictions with the model
predictMSS = predict_point_by_point(data = X_test, model = modelMSS)
print(predictMSS[0:3])

[ 0.00485085  0.00395489  0.00752316]


In [116]:
# Reverse the normalisation
referenceVal = dataBase[rowID:, 0]
y_test_scaled = mv_return_original_scale(norm_val = y_test, base_val = referenceVal)
predictMSS_scaled = mv_return_original_scale(norm_val = predictMSS, base_val = referenceVal)

print(predictMSS_scaled[0:3])
print(y_test_scaled[0:3])

[ 6039.27595196  6321.43876013  6683.40332905]
[ 6481.78666667  6962.62166667  7420.27166667]


In [117]:
# Prepare a vector to act as an ID columns
idData = dataModel.iloc[(rowID + inputSeqLen):-1,:]

# Compare the predictions with the test data
plotResultsMSS = pd.DataFrame({'id': idData.index
                               , 'actual':y_test_scaled
                               , 'predict':predictMSS_scaled})

# Calculate RMSE
rmse = sqrt(mean_squared_error(y_test_scaled, predictMSS_scaled))
print('Test RMSE: %.3f' % rmse)

# Plot the result
plotActuals = go.Scatter(x = plotResultsMSS.id, y = plotResultsMSS.actual, name = "Actuals", mode = 'line')
plotPredicted = go.Scatter(x = plotResultsMSS.id, y = plotResultsMSS.predict, name = "Predicted", mode = 'line')

plotData = [plotActuals, plotPredicted]
plotLayout = go.Layout(title="Actuals vs Predicted - Multivariate, Single-step LSTM",
                xaxis=dict(title='Time (half hour)'),
                yaxis=dict(title='Demand (MW)'))

plotFig = go.Figure(data = plotData, layout = plotLayout)
po.iplot(plotFig)

Test RMSE: 301.080


Comparing this model to the equivalent univariate model, the reduction in error suggests including the temperature variable improves the model's predictive capability.

#### Multivariate multi-step model
* A window of historical demand and air temperature will be used to predict future demand (multivariate)  
* Predictions made using the test data will be used to make predictions for the rest of the sequence (multi-step). This will be initially done using the *mv_predict_sequence_full* function  
* Predictions will also be made on intervals using the *mv_predict_sequences_multiple* function, where sequences of a defined length will be predicted.

In [118]:
# Use true data from the test data for a defined window, and then use model predictions for the rest of the sequence
predictMMS = mv_predict_sequence_full(data = X_test
                                      , model = modelMSS
                                      , window_size = inputSeqLen
                                      , excess_predictors = y_test_x)

Predicting frame
[[ 0.          0.        ]
 [ 0.04765544 -0.02758621]
 [ 0.10372114 -0.04827586]
 ..., 
 [-0.00743246 -0.36551724]
 [-0.00581353 -0.35172414]
 [ 0.02929974 -0.42068966]]
Excess X
-0.393103448276
Row to insert
[0.004850856, -0.39310344827586197]
Predictions
[0.004850856]
Predicting frame
[[ 0.04765544 -0.02758621]
 [ 0.10372114 -0.04827586]
 [ 0.19612165 -0.03448276]
 ..., 
 [-0.00581353 -0.35172414]
 [ 0.02929974 -0.42068966]
 [ 0.00485086 -0.39310345]]
Excess X
-0.340425531915
Row to insert
[0.01503453, -0.34042553191489355]
Predictions
[0.004850856, 0.01503453]


In [119]:
# Reverse the normalisation
predictMMS_scaled = (np.array(predictMMS) + 1) * referenceVal[0]
print(predictMMS_scaled[0:3])
print(y_test_scaled[0:3])

[ 6039.27587891  6100.48095703  6152.00683594]
[ 6481.78666667  6962.62166667  7420.27166667]


In [120]:
# Compare the predictions with the test data
plotResultsMMS = pd.DataFrame({'id': idData.index
                               , 'actual':y_test_scaled
                               , 'predict':predictMMS_scaled})

# Calculate RMSE
rmse = sqrt(mean_squared_error(y_test_scaled, predictMMS_scaled))
print('Test RMSE: %.3f' % rmse)

# Plot the result
plotActuals = go.Scatter(x = plotResultsMMS.id, y = plotResultsMMS.actual, name = "Actuals", mode = 'line')
plotPredicted = go.Scatter(x = plotResultsMMS.id, y = plotResultsMMS.predict, name = "Predicted", mode = 'line')

plotData = [plotActuals, plotPredicted]
plotLayout = go.Layout(title="Actuals vs Predicted - Univariate, Multi-step LSTM - Full sequence prediction",
                xaxis=dict(title='Time (half hour)'),
                yaxis=dict(title='Demand (MW)'))

plotFig = go.Figure(data = plotData, layout = plotLayout)
po.iplot(plotFig)

Test RMSE: 2171.633


Comparing this result to the univariate full sequence prediction, similarly the reduction in RMSE suggests inclusion of air temperature as a variable is improving predictive performance. Also interesting is the the model doesn't revert to a naive forecast like the univariate version. This is likely due to the inclusion of temperature data as a predictor for the entirety of the sequence. 

In [121]:
# Make multi-step predictions, but instead of making a full sequence prediction, predict intervals 
inputPredLen = 48
predictMMS = mv_predict_sequences_multiple(data = X_test
                                        , model = modelMSS
                                        , window_size = inputSeqLen
                                        , prediction_len = inputPredLen
                                        , excess_predictors = y_test_x)
#print(predictUMS[0:3])
predictMMS = np.array(predictMMS)

Starting sequence of true test values
[[ 0.          0.        ]
 [ 0.04765544 -0.02758621]
 [ 0.10372114 -0.04827586]
 ..., 
 [-0.00743246 -0.36551724]
 [-0.00581353 -0.35172414]
 [ 0.02929974 -0.42068966]]
New observations for making predictions
[0.004850856, -0.39310344827586197]
Make a prediction using the model
[0.004850856]
Shifted current frame
[[ 0.04765544 -0.02758621]
 [ 0.10372114 -0.04827586]
 [ 0.19612165 -0.03448276]
 ..., 
 [-0.00743246 -0.36551724]
 [-0.00581353 -0.35172414]
 [ 0.02929974 -0.42068966]]
Filled current frame for next prediction
[[ 0.04765544 -0.02758621]
 [ 0.10372114 -0.04827586]
 [ 0.19612165 -0.03448276]
 ..., 
 [-0.00581353 -0.35172414]
 [ 0.02929974 -0.42068966]
 [ 0.00485086 -0.39310345]]
New observations for making predictions
[0.01503453, -0.34042553191489355]
Make a prediction using the model
[0.004850856, 0.01503453]
Shifted current frame
[[ 0.10372114 -0.04827586]
 [ 0.19612165 -0.03448276]
 [ 0.29812153  0.02068966]
 ..., 
 [-0.00581353 -0.351

New observations for making predictions
[0.10387434, 0.24038461538461542]
Make a prediction using the model
[0.004850856, 0.01503453, 0.023607714, 0.033543922, 0.045720428, 0.053968143, 0.052979343, 0.039901026, 0.02592624, 0.017701454, 0.015092116, 0.021447882, 0.036250472, 0.056768358, 0.079485714, 0.10387434]
Shifted current frame
[[ 0.3065451   0.44827586]
 [ 0.3085897   0.43448276]
 [ 0.31173939  0.44137931]
 ..., 
 [ 0.03625047  0.215     ]
 [ 0.05676836  0.24630542]
 [ 0.07948571  0.23923445]]
Filled current frame for next prediction
[[ 0.3065451   0.44827586]
 [ 0.3085897   0.43448276]
 [ 0.31173939  0.44137931]
 ..., 
 [ 0.05676836  0.24630542]
 [ 0.07948571  0.23923445]
 [ 0.10387434  0.24038462]]
New observations for making predictions
[0.12841825, 0.23809523809523814]
Make a prediction using the model
[0.004850856, 0.01503453, 0.023607714, 0.033543922, 0.045720428, 0.053968143, 0.052979343, 0.039901026, 0.02592624, 0.017701454, 0.015092116, 0.021447882, 0.036250472, 0.05676

New observations for making predictions
[0.21140447, 0.39766081871345005]
Make a prediction using the model
[0.004850856, 0.01503453, 0.023607714, 0.033543922, 0.045720428, 0.053968143, 0.052979343, 0.039901026, 0.02592624, 0.017701454, 0.015092116, 0.021447882, 0.036250472, 0.056768358, 0.079485714, 0.10387434, 0.12841825, 0.15183626, 0.17252737, 0.19043867, 0.20363265, 0.21306562, 0.21999991, 0.22431827, 0.22555499, 0.22358955, 0.21869762, 0.21140447]
Shifted current frame
[[ 0.52634015  0.17241379]
 [ 0.49034947  0.15862069]
 [ 0.45659364  0.14482759]
 ..., 
 [ 0.22555499  0.41798942]
 [ 0.22358955  0.42622951]
 [ 0.21869762  0.42134831]]
Filled current frame for next prediction
[[ 0.52634015  0.17241379]
 [ 0.49034947  0.15862069]
 [ 0.45659364  0.14482759]
 ..., 
 [ 0.22358955  0.42622951]
 [ 0.21869762  0.42134831]
 [ 0.21140447  0.39766082]]
New observations for making predictions
[0.20180658, 0.36470588235294121]
Make a prediction using the model
[0.004850856, 0.01503453, 0.023

New observations for making predictions
[0.023634745, 0.21088435374149661]
Make a prediction using the model
[0.004850856, 0.01503453, 0.023607714, 0.033543922, 0.045720428, 0.053968143, 0.052979343, 0.039901026, 0.02592624, 0.017701454, 0.015092116, 0.021447882, 0.036250472, 0.056768358, 0.079485714, 0.10387434, 0.12841825, 0.15183626, 0.17252737, 0.19043867, 0.20363265, 0.21306562, 0.21999991, 0.22431827, 0.22555499, 0.22358955, 0.21869762, 0.21140447, 0.20180658, 0.18977568, 0.1749422, 0.15739012, 0.13654047, 0.11371439, 0.089971915, 0.066513792, 0.044552024, 0.023634745]
Shifted current frame
[[ 0.27821899 -0.05517241]
 [ 0.24278017 -0.07586207]
 [ 0.21825792 -0.06896552]
 ..., 
 [ 0.08997191  0.21153846]
 [ 0.06651379  0.27027027]
 [ 0.04455202  0.11564626]]
Filled current frame for next prediction
[[ 0.27821899 -0.05517241]
 [ 0.24278017 -0.07586207]
 [ 0.21825792 -0.06896552]
 ..., 
 [ 0.06651379  0.27027027]
 [ 0.04455202  0.11564626]
 [ 0.02363474  0.21088435]]
New observation

New observations for making predictions
[-0.049220908, -0.007812500000000111]
Make a prediction using the model
[0.004850856, 0.01503453, 0.023607714, 0.033543922, 0.045720428, 0.053968143, 0.052979343, 0.039901026, 0.02592624, 0.017701454, 0.015092116, 0.021447882, 0.036250472, 0.056768358, 0.079485714, 0.10387434, 0.12841825, 0.15183626, 0.17252737, 0.19043867, 0.20363265, 0.21306562, 0.21999991, 0.22431827, 0.22555499, 0.22358955, 0.21869762, 0.21140447, 0.20180658, 0.18977568, 0.1749422, 0.15739012, 0.13654047, 0.11371439, 0.089971915, 0.066513792, 0.044552024, 0.023634745, 0.0032807754, -0.017180435, -0.034794707, -0.045590691, -0.051213805, -0.052954968, -0.054135472, -0.049220908]
Shifted current frame
[[ 0.01408291 -0.09655172]
 [ 0.01253053 -0.08965517]
 [ 0.02957649 -0.08965517]
 ..., 
 [-0.0512138   0.12977099]
 [-0.05295497  0.25619835]
 [-0.05413547  0.10909091]]
Filled current frame for next prediction
[[ 0.01408291 -0.09655172]
 [ 0.01253053 -0.08965517]
 [ 0.02957649 -0

New observations for making predictions
[0.06109006, 0.42331288343558282]
Make a prediction using the model
[-0.0084259044, 0.0036134415, 0.016536225, 0.031339217, 0.047143672, 0.056253538, 0.056368839, 0.052022208, 0.051212039, 0.06109006]
Shifted current frame
[[ 0.29279118  0.28030303]
 [ 0.27840822  0.33333333]
 [ 0.26774867  0.4469697 ]
 ..., 
 [ 0.05636884  0.43846154]
 [ 0.05202221  0.51879699]
 [ 0.05121204  0.48322148]]
Filled current frame for next prediction
[[ 0.29279118  0.28030303]
 [ 0.27840822  0.33333333]
 [ 0.26774867  0.4469697 ]
 ..., 
 [ 0.05202221  0.51879699]
 [ 0.05121204  0.48322148]
 [ 0.06109006  0.42331288]]
New observations for making predictions
[0.082101785, 0.49112426035502965]
Make a prediction using the model
[-0.0084259044, 0.0036134415, 0.016536225, 0.031339217, 0.047143672, 0.056253538, 0.056368839, 0.052022208, 0.051212039, 0.06109006, 0.082101785]
Shifted current frame
[[ 0.27840822  0.33333333]
 [ 0.26774867  0.4469697 ]
 [ 0.25792005  0.4469697 

New observations for making predictions
[0.27332217, 0.40284360189573465]
Make a prediction using the model
[-0.0084259044, 0.0036134415, 0.016536225, 0.031339217, 0.047143672, 0.056253538, 0.056368839, 0.052022208, 0.051212039, 0.06109006, 0.082101785, 0.1075367, 0.13521306, 0.16537522, 0.19453625, 0.22103485, 0.24336267, 0.26080719, 0.27274871, 0.27878812, 0.27843791, 0.27332217]
Shifted current frame
[[ 0.23837324  0.62121212]
 [ 0.26259532  0.57575758]
 [ 0.28395751  0.53030303]
 ..., 
 [ 0.27274871  0.41626794]
 [ 0.27878812  0.39719626]
 [ 0.27843791  0.41203704]]
Filled current frame for next prediction
[[ 0.23837324  0.62121212]
 [ 0.26259532  0.57575758]
 [ 0.28395751  0.53030303]
 ..., 
 [ 0.27878812  0.39719626]
 [ 0.27843791  0.41203704]
 [ 0.27332217  0.4028436 ]]
New observations for making predictions
[0.26379025, 0.36448598130841137]
Make a prediction using the model
[-0.0084259044, 0.0036134415, 0.016536225, 0.031339217, 0.047143672, 0.056253538, 0.056368839, 0.0520222

New observations for making predictions
[0.063980684, 0.46794871794871784]
Make a prediction using the model
[-0.0084259044, 0.0036134415, 0.016536225, 0.031339217, 0.047143672, 0.056253538, 0.056368839, 0.052022208, 0.051212039, 0.06109006, 0.082101785, 0.1075367, 0.13521306, 0.16537522, 0.19453625, 0.22103485, 0.24336267, 0.26080719, 0.27274871, 0.27878812, 0.27843791, 0.27332217, 0.26379025, 0.25017342, 0.23328985, 0.21323442, 0.19013369, 0.16559711, 0.13965638, 0.11355292, 0.087709799, 0.063980684]
Shifted current frame
[[ 0.33373196  0.16666667]
 [ 0.30693684 -0.02272727]
 [ 0.28110597  0.02272727]
 ..., 
 [ 0.13965638  0.47590361]
 [ 0.11355292  0.48765432]
 [ 0.0877098   0.43209877]]
Filled current frame for next prediction
[[ 0.33373196  0.16666667]
 [ 0.30693684 -0.02272727]
 [ 0.28110597  0.02272727]
 ..., 
 [ 0.11355292  0.48765432]
 [ 0.0877098   0.43209877]
 [ 0.06398068  0.46794872]]
New observations for making predictions
[0.04321852, 0.53896103896103886]
Make a predicti

New observations for making predictions
[0.026263036, 1.2777777777777777]
Make a prediction using the model
[-0.0084259044, 0.0036134415, 0.016536225, 0.031339217, 0.047143672, 0.056253538, 0.056368839, 0.052022208, 0.051212039, 0.06109006, 0.082101785, 0.1075367, 0.13521306, 0.16537522, 0.19453625, 0.22103485, 0.24336267, 0.26080719, 0.27274871, 0.27878812, 0.27843791, 0.27332217, 0.26379025, 0.25017342, 0.23328985, 0.21323442, 0.19013369, 0.16559711, 0.13965638, 0.11355292, 0.087709799, 0.063980684, 0.04321852, 0.025077634, 0.0091757709, -0.0011128017, -0.0059437975, -0.0053923996, -6.402866e-05, 0.0087866271, 0.017808959, 0.026263036]
Shifted current frame
[[  1.32991698e-01  -3.18181818e-01]
 [  8.07524817e-02  -3.03030303e-01]
 [  2.90433342e-02  -3.48484848e-01]
 ..., 
 [ -6.40286598e-05   8.72727273e-01]
 [  8.78662709e-03   1.16831683e+00]
 [  1.78089589e-02   1.14583333e+00]]
Filled current frame for next prediction
[[ 0.1329917  -0.31818182]
 [ 0.08075248 -0.3030303 ]
 [ 0.02

In [122]:
predictMMS_scaled, newRowDim = return_original_scale_multiple(norm_val = predictMMS
                                                              , base_val = referenceVal
                                                              , prediction_len = inputPredLen)

In [123]:
# Trim the arrays for incomplete sequences
idData = idData.iloc[0:newRowDim]
y_test_scaled_trim = y_test_scaled[0:newRowDim]

# Calculate RMSE
rmse = sqrt(mean_squared_error(y_test_scaled_trim, predictMMS_scaled))
print('Test RMSE: %.3f' % rmse)

# Compare the predictions with the test data
plotResultsMMS = pd.DataFrame({'id': idData.index
                               , 'actual':y_test_scaled_trim
                               , 'predict':predictMMS_scaled})

# Plot the result
plotActuals = go.Scatter(x = plotResultsMMS.id, y = plotResultsMMS.actual, name = "Actuals", mode = 'line')
plotPredicted = go.Scatter(x = plotResultsMMS.id, y = plotResultsMMS.predict, name = "Predicted", mode = 'line')

plotData = [plotActuals, plotPredicted]
plotLayout = go.Layout(title="Actuals vs Predicted - Multivariate, Multi-step LSTM - Predicting sequences of x periods",
                xaxis=dict(title='Time (half hour)'),
                yaxis=dict(title='Demand (MW)'))

plotFig = go.Figure(data = plotData, layout = plotLayout)
po.iplot(plotFig)

Test RMSE: 1277.264


Comparing this result to the univariate equivalent, the model has improved with the inclusion of air temperature as a predictor.  

In [124]:
os.system('jupyter nbconvert --to html PredictingDemand.ipynb')

0